# Manual Identifier Conversion Example

In [1]:
0

0

In [2]:
%load_ext autoreload
%autoreload 2

In [3]:
import sys

sys.path.append("/home/icb/kemal.inecik/work/codes/idtrack")

In [4]:
import os
import pickle
import subprocess
import time

import idtrack
import pandas as pd
import scanpy as sc

Initialize the graph and pathfinder

In [5]:
local_dir = "/lustre/groups/ml01/workspace/kemal.inecik/idtrack_temp"
test_results_dir = os.path.join(local_dir, "hlca")

idt = idtrack.API(local_repository=local_dir)
idt.configure_logger()
idt.initialize_graph(organism_name="homo_sapiens", last_ensembl_release=114, return_test=True)

2025-06-01 08:40:55 INFO:graph_maker: The graph is being read: /lustre/groups/ml01/workspace/kemal.inecik/idtrack_temp/graph_homo_sapiens_min79_max114_narrow.pickle


In [6]:
idt.calculate_graph_caches()

2025-06-01 08:41:47 INFO:the_graph: Cached properties being calculated: combined_edges


2025-06-01 08:42:19 INFO:the_graph: Cached properties being calculated: combined_edges_assembly_specific_genes


2025-06-01 08:42:22 INFO:the_graph: Cached properties being calculated: combined_edges_genes


2025-06-01 08:42:34 INFO:the_graph: Cached properties being calculated: lower_chars_graph


2025-06-01 08:42:34 INFO:the_graph: Cached properties being calculated: get_active_ranges_of_id


...

2025-06-01 08:43:11 INFO:the_graph: Cached properties being calculated: available_external_databases_assembly


2025-06-01 08:43:12 INFO:the_graph: Cached properties being calculated: node_trios


2025-06-01 08:43:28 INFO:the_graph: Cached properties being calculated: hyperconnective_nodes


2025-06-01 08:43:31 INFO:the_graph: Cached properties being calculated (for tests): external_database_connection_form


2025-06-01 08:44:16 INFO:the_graph: Cached properties being calculated (for tests): available_releases_given_database_assembly


The datasets of HLCA

In [7]:
base_path = "/lustre/groups/ml01/projects/2023_HLCA_LSikkema/HLCA_reproducibility/data"
dset0_dir = os.path.join(base_path, "HLCA_extended/extension_datasets/ready/full")
dset1_dir = os.path.join(base_path, "HLCA_extended/extension_datasets/raw")

adata_dict = {
    "Kaminski_2020": [f"{dset0_dir}/adams.h5ad"],
    "Meyer_2021": [f"{dset0_dir}/meyer_2021.h5ad"],
    "MeyerNikolic_unpubl": [f"{dset0_dir}/meyer_nikolic_unpubl.h5ad"],
    "Barbry_unpubl": [f"{dset0_dir}/barbry.h5ad"],
    "Regev_2021": [
        f"{dset0_dir}/delorey_cryo.h5ad",
        f"{dset0_dir}/delorey_fresh.h5ad",
        f"{dset0_dir}/delorey_nuclei.h5ad",
    ],
    "Thienpont_2018": [f"{dset1_dir}/Lambrechts/lambrechts.h5ad"],
    "Budinger_2020": [f"{dset0_dir}/bharat.h5ad"],
    "Banovich_Kropski_2020": [f"{dset0_dir}/haberman.h5ad"],
    "Sheppard_2020": [f"{dset0_dir}/tsukui.h5ad"],
    "Wunderink_2021": [f"{dset0_dir}/grant_cryo.h5ad", f"{dset0_dir}/grant_fresh.h5ad"],
    "Lambrechts_2021": [f"{dset0_dir}/wouters.h5ad"],  # , f"{dset0_dir}/wouters_labs.h5ad"
    "Zhang_2021": [f"{dset1_dir}/Liao/covid_for_publish.h5ad"],
    "Duong_lungMAP_unpubl": [f"{dset0_dir}/duong.h5ad"],
    "Janssen_2020": [f"{dset0_dir}/mould.h5ad"],
    "Sun_2020": [
        f"{dset0_dir}/wang_sub_batch1.h5ad",
        f"{dset0_dir}/wang_sub_batch2.h5ad",
        f"{dset0_dir}/wang_sub_batch3.h5ad",
        f"{dset0_dir}/wang_sub_batch4.h5ad",
    ],
    "Gomperts_2021": [
        f"{dset0_dir}/carraro_ucla.h5ad",
        f"{dset0_dir}/carraro_cff.h5ad",
        f"{dset0_dir}/carraro_csmc.h5ad",
    ],
    "Eils_2020": [f"{dset0_dir}/lukassen.h5ad"],
    "Schiller_2020": [f"{dset0_dir}/mayr.h5ad"],
    "Misharin_Budinger_2018": [f"{dset0_dir}/reyfman_disease.h5ad"],
    "Shalek_2018": [f"{dset0_dir}/ordovasmontanes.h5ad"],
    "Schiller_2021": [f"{dset0_dir}/schiller_discovair.h5ad"],
    "Peer_Massague_2020": [f"{dset0_dir}/laughney.h5ad"],
    "Lafyatis_2019": [f"{dset0_dir}/valenzi.h5ad"],
    "Tata_unpubl": [f"{dset0_dir}/tata_unpubl.h5ad"],
    "Xu_2020": [f"{dset0_dir}/guo.h5ad"],
    "Sims_2019": [f"{dset0_dir}/szabo.h5ad"],
    "Schultze_unpubl": [f"{dset0_dir}/schultze_unpubl.h5ad"],
}

Run the ID conversion with HGNC Symbol (a.k.a gene name)

In [8]:
result = dict()
final_database = "HGNC Symbol"

for dataset_name in adata_dict:

    adata = sc.read(adata_dict[dataset_name][0])
    gene_list = list(adata.var.index)

    matching = idt.convert_identifier_multiple(
        gene_list, final_database=final_database, to_release=107, pbar_prefix=dataset_name
    )
    binned_conversions = idt.classify_multiple_conversion(matching)

    idt.print_binned_conversion(binned_conversions)
    print(f"Source release: {idt.infer_identifier_source(gene_list)}")

    result[dataset_name] = binned_conversions

Kaminski_2020:   0%|          | 0/45947 [00:00<?, ?it/s]

Kaminski_2020:   0%|          | 19/45947 [00:00<12:08, 63.02it/s, ID:KRIT1]

Kaminski_2020:   0%|          | 35/45947 [00:00<13:09, 58.16it/s, ID:CYP26B1]

Kaminski_2020:   0%|          | 57/45947 [00:00<10:59, 69.62it/s, ID:VPS50]  

Kaminski_2020:   0%|          | 86/45947 [00:01<08:54, 85.77it/s, ID:FAM214B]

...

Schultze_unpubl:  99%|█████████▉| 24272/24532 [04:21<00:00, 443.26it/s, ID:UBA52P7] 

Schultze_unpubl: 100%|█████████▉| 24476/24532 [04:21<00:00, 542.30it/s, ID:HTT-AS] 

Schultze_unpubl: 100%|██████████| 24532/24532 [04:21<00:00, 93.66it/s, ID:AP001269.4]


2025-06-01 19:21:57 INFO:api: changed_only_1_to_n: 0
changed_only_1_to_1: 2036
alternative_target_1_to_1: 3874
alternative_target_1_to_n: 13
matching_1_to_0: 42
matching_1_to_1: 20603
matching_1_to_n: 0
input_identifiers: 24532


Source release: (38, 91)


In [9]:
os.makedirs(test_results_dir, exist_ok=True)
file_path = os.path.join(test_results_dir, f"results_for_hlca_datasets_{final_database}.pk")
with open(file_path, "wb") as handle:
    pickle.dump(result, handle)
print(f"Saved: {file_path}")

Saved: /lustre/groups/ml01/workspace/kemal.inecik/idtrack_temp/hlca/results_for_hlca_datasets_HGNC Symbol.pk


Run the ID conversion with Ensembl gene ID

In [10]:
result = dict()
final_database = "ensembl_gene"

for dataset_name in adata_dict:

    adata = sc.read(adata_dict[dataset_name][0])
    gene_list = list(adata.var.index)

    matching = idt.convert_identifier_multiple(
        gene_list, final_database=final_database, to_release=107, pbar_prefix=dataset_name
    )
    binned_conversions = idt.classify_multiple_conversion(matching)

    idt.print_binned_conversion(binned_conversions)
    print(f"Source release: {idt.infer_identifier_source(gene_list)}")

    result[dataset_name] = binned_conversions

Kaminski_2020:   0%|          | 0/45947 [00:00<?, ?it/s]

Kaminski_2020:   0%|          | 21/45947 [00:00<10:47, 70.96it/s, ID:MYH16]

Kaminski_2020:   0%|          | 62/45947 [00:00<06:17, 121.50it/s, ID:ZMYND10]

Kaminski_2020:   0%|          | 101/45947 [00:00<05:37, 135.70it/s, ID:ZNF195]

Kaminski_2020:   0%|          | 142/45947 [00:01<05:18, 143.66it/s, ID:IFRD1] 

...

Schultze_unpubl:  99%|█████████▊| 24171/24532 [02:57<00:00, 611.24it/s, ID:ASB15] 

Schultze_unpubl: 100%|█████████▉| 24463/24532 [02:58<00:00, 733.82it/s, ID:AC022509.1]

Schultze_unpubl: 100%|██████████| 24532/24532 [02:58<00:00, 137.78it/s, ID:AP001269.4]


2025-06-01 21:47:49 INFO:api: changed_only_1_to_n: 202
changed_only_1_to_1: 24288
alternative_target_1_to_1: 0
alternative_target_1_to_n: 0
matching_1_to_0: 42
matching_1_to_1: 24288
matching_1_to_n: 202
input_identifiers: 24532


Source release: (38, 91)


In [11]:
os.makedirs(test_results_dir, exist_ok=True)
file_path = os.path.join(test_results_dir, f"results_for_hlca_datasets_{final_database}.pk")
with open(file_path, "wb") as handle:
    pickle.dump(result, handle)
print(f"Saved: {file_path}")

Saved: /lustre/groups/ml01/workspace/kemal.inecik/idtrack_temp/hlca/results_for_hlca_datasets_ensembl_gene.pk


Print the processor

In [12]:
print((subprocess.check_output("lscpu", shell=True).strip()).decode())

Architecture:                       x86_64
CPU op-mode(s):                     32-bit, 64-bit
Address sizes:                      52 bits physical, 57 bits virtual
Byte Order:                         Little Endian
CPU(s):                             224
On-line CPU(s) list:                0-223
Vendor ID:                          GenuineIntel
Model name:                         Intel(R) Xeon(R) Platinum 8480+
CPU family:                         6
Model:                              143
Thread(s) per core:                 2
Core(s) per socket:                 56
Socket(s):                          2
Stepping:                           8
CPU(s) scaling MHz:                 100%
CPU max MHz:                        3800.0000
CPU min MHz:                        800.0000
BogoMIPS:                           4000.00
Flags:                              fpu vme de pse tsc msr pae mce cx8 apic sep mtrr pge mca cmov pat pse36 clflush dts acpi mmx fxsr sse sse2 ss ht tm pbe syscall nx pdpe1gb rdtsc

Plot/Table

In [13]:
!ls -lh /lustre/groups/ml01/workspace/kemal.inecik/idtrack_temp

total 41G
-rw-r--r--. 1 kemal.inecik OG-ICB-User 813M May 27 20:30 graph_homo_sapiens_min79_max114_narrow.pickle
drwxr-xr-x. 2 kemal.inecik OG-ICB-User 4.0K Jun  1 21:47 hlca
-rw-r--r--. 1 kemal.inecik OG-ICB-User  20G May 27 20:28 homo_sapiens_assembly-37.h5
-rw-r--r--. 1 kemal.inecik OG-ICB-User  20G May 27 20:28 homo_sapiens_assembly-38.h5
-rw-r--r--. 1 kemal.inecik OG-ICB-User  64K May 27 17:59 homo_sapiens_externals_modified.yml
-rw-r--r--. 1 kemal.inecik OG-ICB-User  54K May 27 17:26 homo_sapiens_externals_template.yml
drwxr-xr-x. 2 kemal.inecik OG-ICB-User 4.0K Jun  1 09:16 tests


In [14]:
with open(os.path.join(test_results_dir, "results_for_hlca_datasets_ensembl_gene.pk"), "rb") as pickle_file_1:
    res_ens = pickle.load(pickle_file_1)
with open(os.path.join(test_results_dir, "results_for_hlca_datasets_HGNC Symbol.pk"), "rb") as pickle_file_2:
    res_hgn = pickle.load(pickle_file_2)

In [15]:
r_ens = dict()
for i in res_ens:
    r_ens[i] = dict()
    for j in res_ens[i]:
        r_ens[i][j] = len(res_ens[i][j])

r_hgn = dict()
for i in res_hgn:
    r_hgn[i] = dict()
    for j in res_hgn[i]:
        r_hgn[i][j] = len(res_hgn[i][j])

In [16]:
column_order = [
    "input_identifiers",
    "matching_1_to_1",
    "changed_only_1_to_1",
    "alternative_target_1_to_1",
    "matching_1_to_n",
    "changed_only_1_to_n",
    "alternative_target_1_to_n",
    "matching_1_to_0",
]
raname_columns = {
    "input_identifiers": "",
    "matching_1_to_1": "TDM",
    "changed_only_1_to_1": "CI",
    "alternative_target_1_to_1": "ATM",  # TDM: target database matching, ATM: alternative target matching
    "matching_1_to_n": "TDM",
    "changed_only_1_to_n": "CI",
    "alternative_target_1_to_n": "ATM",
    "matching_1_to_0": "",
}
higher_columns = [
    "Input IDs",
    "One-to-One",
    "One-to-One",
    "One-to-One",
    "One-to-Many",
    "One-to-Many",
    "One-to-Many",
    "One-to-None",
]

In [17]:
df1 = pd.DataFrame.from_dict(r_hgn).T[column_order].rename(columns=raname_columns)
df1.columns = [[""] + ["Target HGNC Names"] * 6 + [""], higher_columns, df1.columns]
df2 = pd.DataFrame.from_dict(r_ens).T[column_order].rename(columns=raname_columns)
df2.columns = [[""] + ["Target Ensembl"] * 6 + [""], higher_columns, df2.columns]

In [18]:
df = pd.concat([df1, df2[["Target Ensembl"]]], axis=1)

In [19]:
df = df[
    [
        ("", "Input IDs", ""),
        ("Target HGNC Names", "One-to-One", "TDM"),
        # ('Target HGNC Names',  'One-to-One',        'CI'),
        ("Target HGNC Names", "One-to-One", "ATM"),
        ("Target HGNC Names", "One-to-Many", "TDM"),
        # ('Target HGNC Names', 'One-to-Many',        'CI'),
        ("Target HGNC Names", "One-to-Many", "ATM"),
        ("Target Ensembl", "One-to-One", "TDM"),
        # (   'Target Ensembl',  'One-to-One',        'CI'),
        # (   'Target Ensembl',  'One-to-One',       'ATM'),
        ("Target Ensembl", "One-to-Many", "TDM"),
        # (   'Target Ensembl', 'One-to-Many',        'CI'),
        # (   'Target Ensembl', 'One-to-Many',       'ATM'),
        ("", "One-to-None", ""),
    ]
]
df

Target HGNC Names                          \
                       Input IDs        One-to-One        One-to-Many        
                                               TDM    ATM         TDM  ATM   
Kaminski_2020              45947             33648  12037          51  117   
Meyer_2021                 20922             20555    349           0    4   
MeyerNikolic_unpubl        33582             25025   8438           4   16   
Barbry_unpubl              16859             15150   1687           0    5   
Regev_2021                 30983             23388   7471           2   14   
Thienpont_2018             27958             22499   5250           1   40   
Budinger_2020              26316             21389   4866           2    7   
Banovich_Kropski_2020      33694             25371   8011           3   53   
Sheppard_2020              27147             22002   4944           1   37   
Wunderink_2021             21819             18809   2956           1    2   
Lambrechts_2021            33538             25007   8438           4   16   
Zhang_2021                 18474             18375     90           0    1   
Duong_lungMAP_unpubl       27678             21552   6062           2   14   
Janssen_2020               33538             25007   8438           4   16   
Sun_2020                   26578             21042   5477           2   11   
Gomperts_2021              31229             24926   5941           6   30   
Eils_2020                  32738             24778   7325           5   41   
Schiller_2020              32104             25153   6421           1   23   
Misharin_Budinger_2018     27181             22036   4929           1   41   
Shalek_2018                25328             21273   3554           2   31   
Schiller_2021              17533             17312    213           0    0   
Peer_Massague_2020         19222             17928   1223           0   11   
Lafyatis_2019              22164             21715    426           2    4   
Tata_unpubl                31915             24232   7636           4   11   
Xu_2020                    32738             24778   7325           5   41   
Sims_2019                  60725             42473  16375         156  280   
Schultze_unpubl            24532             20603   3874           0   13   

                       Target Ensembl                          
                           One-to-One One-to-Many One-to-None  
                                  TDM         TDM              
Kaminski_2020                   45253         600          94  
Meyer_2021                      20688         220          14  
MeyerNikolic_unpubl             33169         314          99  
Barbry_unpubl                   16736         106          17  
Regev_2021                      30644         231         108  
Thienpont_2018                  27548         242         168  
Budinger_2020                   26066         198          52  
Banovich_Kropski_2020           33094         344         256  
Sheppard_2020                   26751         233         163  
Wunderink_2021                  21596         172          51  
Lambrechts_2021                 33151         314          73  
Zhang_2021                      18303         163           8  
Duong_lungMAP_unpubl            27443         187          48  
Janssen_2020                    33151         314          73  
Sun_2020                        26366         166          46  
Gomperts_2021                   30625         278         326  
Eils_2020                       31870         279         589  
Schiller_2020                   31334         264         506  
Misharin_Budinger_2018          26760         247         174  
Shalek_2018                     24663         197         468  
Schiller_2021                   17387         138           8  
Peer_Massague_2020              19009         153          60  
Lafyatis_2019                   21871         276          17  
Tata_unpubl                 

In [20]:
query_ids = dict()
for i in res_hgn:
    query_ids[i] = list()
    for j in res_hgn[i]["input_identifiers"]:
        query_ids[i].append(j["query_id"])

hgnc_ids = dict()
for i in res_hgn:
    hgnc_ids[i] = list()
    for j in res_hgn[i]["matching_1_to_1"]:
        hgnc_ids[i].append(j["target_id"][0])
    for j in res_hgn[i]["alternative_target_1_to_1"]:
        hgnc_ids[i].append(j["target_id"][0])

ens_ids = dict()
for i in res_ens:
    ens_ids[i] = list()
    for j in res_ens[i]["matching_1_to_1"]:
        ens_ids[i].append(j["target_id"][0])

In [21]:
for i in query_ids:
    print(len(query_ids[i]), len(hgnc_ids[i]), len(ens_ids[i]))

45947 45685 45253
20922 20904 20688
33582 33463 33169
16859 16837 16736
30983 30859 30644
27958 27749 27548
26316 26255 26066
33694 33382 33094
27147 26946 26751
21819 21765 21596
33538 33445 33151
18474 18465 18303
27678 27614 27443
33538 33445 33151
26578 26519 26366
31229 30867 30625
32738 32103 31870
32104 31574 31334
27181 26965 26760
25328 24827 24663
17533 17525 17387
19222 19151 19009
22164 22141 21871
31915 31868 31579
32738 32103 31870
60725 58848 58254
24532 24477 24288


In [22]:
a1 = [i for k, v in query_ids.items() for i in v]
a2 = [i for k, v in hgnc_ids.items() for i in v]
a3 = [i for k, v in ens_ids.items() for i in v]
len(a1), len(a2), len(a3)

(782442, 775782, 769469)

In [23]:
b1, b2, b3 = set(a1), set(a2), set(a3)
len(b1), len(b2), len(b3)

(94538, 57115, 56261)

In [24]:
[(i, len(b3 - set(v)), len(set(v)), len(b3)) for i, v in ens_ids.items()]

[('Kaminski_2020', 12042, 44219, 56261),
 ('Meyer_2021', 35858, 20403, 56261),
 ('MeyerNikolic_unpubl', 24102, 32159, 56261),
 ('Barbry_unpubl', 39680, 16581, 56261),
 ('Regev_2021', 26351, 29910, 56261),
 ('Thienpont_2018', 29365, 26896, 56261),
 ('Budinger_2020', 30722, 25539, 56261),
 ('Banovich_Kropski_2020', 24197, 32064, 56261),
 ('Sheppard_2020', 30133, 26128, 56261),
 ('Wunderink_2021', 35024, 21237, 56261),
 ('Lambrechts_2021', 24102, 32159, 56261),
 ('Zhang_2021', 38117, 18144, 56261),
 ('Duong_lungMAP_unpubl', 29367, 26894, 56261),
 ('Janssen_2020', 24102, 32159, 56261),
 ('Sun_2020', 30384, 25877, 56261),
 ('Gomperts_2021', 30839, 25422, 56261),
 ('Eils_2020', 25684, 30577, 56261),
 ('Schiller_2020', 28554, 27707, 56261),
 ('Misharin_Budinger_2018', 30132, 26129, 56261),
 ('Shalek_2018', 32168, 24093, 56261),
 ('Schiller_2021', 39030, 17231, 56261),
 ('Peer_Massague_2020', 37486, 18775, 56261),
 ('Lafyatis_2019', 34779, 21482, 56261),
 ('Tata_unpubl', 25382, 30879, 56261),


In [25]:
[(i, len(b2 - set(v)), len(set(v)), len(b2)) for i, v in hgnc_ids.items()]

[('Kaminski_2020', 12390, 44725, 57115),
 ('Meyer_2021', 36328, 20787, 57115),
 ('MeyerNikolic_unpubl', 24393, 32722, 57115),
 ('Barbry_unpubl', 40379, 16736, 57115),
 ('Regev_2021', 26822, 30293, 57115),
 ('Thienpont_2018', 29868, 27247, 57115),
 ('Budinger_2020', 31245, 25870, 57115),
 ('Banovich_Kropski_2020', 24551, 32564, 57115),
 ('Sheppard_2020', 30658, 26457, 57115),
 ('Wunderink_2021', 35604, 21511, 57115),
 ('Lambrechts_2021', 24393, 32722, 57115),
 ('Zhang_2021', 38719, 18396, 57115),
 ('Duong_lungMAP_unpubl', 29939, 27176, 57115),
 ('Janssen_2020', 24393, 32722, 57115),
 ('Sun_2020', 30975, 26140, 57115),
 ('Gomperts_2021', 31215, 25900, 57115),
 ('Eils_2020', 26120, 30995, 57115),
 ('Schiller_2020', 29102, 28013, 57115),
 ('Misharin_Budinger_2018', 30630, 26485, 57115),
 ('Shalek_2018', 32792, 24323, 57115),
 ('Schiller_2021', 39646, 17469, 57115),
 ('Peer_Massague_2020', 38108, 19007, 57115),
 ('Lafyatis_2019', 35122, 21993, 57115),
 ('Tata_unpubl', 25670, 31445, 57115),


In [26]:
[(i, len(b1 - set(v)), len(set(v)), len(b1)) for i, v in query_ids.items()]

[('Kaminski_2020', 48591, 45947, 94538),
 ('Meyer_2021', 73616, 20922, 94538),
 ('MeyerNikolic_unpubl', 60956, 33582, 94538),
 ('Barbry_unpubl', 77679, 16859, 94538),
 ('Regev_2021', 63555, 30983, 94538),
 ('Thienpont_2018', 66580, 27958, 94538),
 ('Budinger_2020', 68222, 26316, 94538),
 ('Banovich_Kropski_2020', 60844, 33694, 94538),
 ('Sheppard_2020', 67391, 27147, 94538),
 ('Wunderink_2021', 72719, 21819, 94538),
 ('Lambrechts_2021', 61000, 33538, 94538),
 ('Zhang_2021', 76064, 18474, 94538),
 ('Duong_lungMAP_unpubl', 66860, 27678, 94538),
 ('Janssen_2020', 61000, 33538, 94538),
 ('Sun_2020', 67960, 26578, 94538),
 ('Gomperts_2021', 63309, 31229, 94538),
 ('Eils_2020', 61800, 32738, 94538),
 ('Schiller_2020', 62434, 32104, 94538),
 ('Misharin_Budinger_2018', 67357, 27181, 94538),
 ('Shalek_2018', 69210, 25328, 94538),
 ('Schiller_2021', 77005, 17533, 94538),
 ('Peer_Massague_2020', 75316, 19222, 94538),
 ('Lafyatis_2019', 72374, 22164, 94538),
 ('Tata_unpubl', 62623, 31915, 94538),


In [27]:
1

1